In [ ]:
!pip -q install git+https://github.com/huggingface/transformers.git
!pip -q install peft
!pip -q install accelerate
!pip -q install sentencepiece
!pip -q install bitsandbytes

In [ ]:
from IPython.display import Markdown as md

import transformers
import peft
import accelerate
import bitsandbytes

print(transformers.__version__)
print(peft.__version__)
print(accelerate.__version__)


In [2]:
import torch
from peft import PeftModel
from transformers import LlamaTokenizer, LlamaForCausalLM

def load_model(base, finetuned):
    tokenizer = LlamaTokenizer.from_pretrained(base)
    tokenizer.pad_token_id = 0
    tokenizer.padding_side = "left"

    model = LlamaForCausalLM.from_pretrained(
        base,
        load_in_8bit=True,
        device_map="auto",
    )
    
    model = PeftModel.from_pretrained(
        model, 
        finetuned,
        device_map={'': 0}
    )
    return model, tokenizer

def get_output_batch(
    model, tokenizer, prompt, generation_config, device='cuda'
):
  encoding = tokenizer(prompt, return_tensors="pt")
  input_ids = encoding["input_ids"].to(device)
  generated_id = model.generate(
      input_ids=input_ids,
      generation_config=generation_config,
      max_new_tokens=256
  )

  decoded = tokenizer.batch_decode(
      generated_id, skip_prompt=True, skip_special_tokens=True
  )
  del input_ids, generated_id
  torch.cuda.empty_cache()
  return decoded[0].split("### Response:")[-1]

### AlpacaGPT4-LoRA 7B (05/01)

In [3]:
from transformers import GenerationConfig

base = "elinas/llama-7b-hf-transformers-4.29"
sft = "LLMs/AlpacaGPT4-LoRA-7B-elina"

genConfig = GenerationConfig(
    temperature=0.95,
    top_p=0.9,
    top_k=50,
    num_beams=1,
    repetition_penalty=1.2,
    max_new_token=2048,
    do_sample=True,
)

In [4]:
model, tokenizer = load_model(base, sft)

Overriding torch_dtype=None with `torch_dtype=torch.float16` due to requirements of `bitsandbytes` to enable model loading in mixed int8. Either pass torch_dtype=torch.float16 or don't pass this argument at all to remove this warning.


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [5]:
prompt = """### Instruction: Compose an engaging travel blog post about a recent trip to Hawaii, highlighting cultural experiences and must-see attractions.

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Dear Travelers, <br />Have you ever wondered what it's like to step foot on one of the most famous islands in the world? Have you dreamt of experiencing its natural beauty and exotic culture? Well, here at Explorify we have just returned from our epic journey to paradise - HAWAII! As experienced tourists and avid explorers ourselves, we had the opportunity to embark upon the adventure of a lifetime and bring back some truly unforgettable memories. Our first stop was Oahu Island where we visited numerous locations such as Diamond Head State Monument, The Pali Lookout & Nu’uanu Valley Overlook for panoramic views over Honolulu, Waikiki Beach, Kualoa Regional Park with lush greenery and picturesque valleys all around us. We took part in many activities including hiking through breathtaking trails, snorkeling and swimming in crystal clear waters surrounded by colorful marine life and fishes while enjoying magnificent underwater scenes. In addition to visiting Pearl Harbor Memorial and witnessing military history up close, we also went deep sea fishing aboard cat

In [6]:
prompt = """### Instruction: Can you help me write a formal email to a potential business partner proposing a joint venture?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Dear [Partner Name], <br /><br />We are excited about the prospect of creating a new partnership with your organization and we hope that this letter serves as an opportunity for us to discuss in detail our proposal. We at Company X have been researching various options available to expand our service offerings, and we believe that a joint venture would be mutually beneficial. As part of the collaboration, both parties will receive a share of profits based on their respective contributions made towards achieving common goals such as increasing market penetration, improving efficiency and reducing costs while maintaining high-quality standards. In addition, each company can leverage its expertise to create value for customers through innovative products or services. Finally, the resulting synergy between our two organizations is expected to deliver long-term benefits.

In [7]:
prompt = """### Instruction: Can you help me write a resignation letter to my current employer, while leaving on good terms and expressing gratitude for the opportunities provided?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 Dear [Name of Employer],<br /><br />After much consideration, I regretfully inform you that I will be ending my employment with your company. It has been an honor working alongside all of you during this time, and it is with great sadness that I must move forward from this position. <br /><br />My decision was not made lightly; I have greatly appreciated being given the opportunity to grow professionally as well as personally in this role. You have helped fostered an environment where collaboration and teamwork are valued, and the knowledge that we each bring together creates innovative solutions every day. Thank you for providing me with a supportive workplace, challenges, learning experiences, and personal growth throughout these years. <br /><br />In closing, know that even though I am stepping away, our relationship remains important and valuable to both parties involved. Please accept this letter as both my resignation but also my sincere appreciation and wish for continued success within the organization.

In [8]:
prompt = """### Instruction: How can you determine if a restaurant is popular among locals or mainly attracts tourists, and why might this information be useful?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 <br />If a restaurant is primarily visited by local residents rather than tourist it means that the food offered there has been reviewed positively on social media and shared through word-of-mouth recommendations. It also means that they have established themselves as an authentic local establishment in the area where people would visit for their favorite dishes. This kind of restaurant provides more memorable experiences to visitors since they are able to taste real local cuisine that cannot be found elsewhere. On the other hand, restaurants aiming at tourism may offer overpriced meals with exotic ingredients from far away places which don't really appeal to most people living locally but appealed to many travelers. A restaurant being mostly frequented by locals indicates a higher likelihood of providing quality local fare, unique flavors, and authentic atmosphere, making them ideal destinations for those looking to experience true culinary culture.

In [9]:
prompt = """### Instruction: What are some subtle clues that suggest someone is pretending to understand a topic or conversation when they are actually confused or uninformed?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 Here are five possible subtleties indicating that a person may be feigning comprehension on the subject matter, without really understanding it. <br />1) Avoidance of direct questions about details and specifics - This can signal that the individual does not have much information or knowledge to share but wants to appear informed in order to avoid being exposed as having limited expertise.<br />2) Speaking confidently despite gaps in their knowledge - Someone who knows little about something could try to compensate by appearing authoritative through confidence alone, perhaps using technical language or jargon in an attempt to sound like an expert even though they do not fully grasp what is being discussed. <br />3) Failure to recognize when others clarify unclear statements with further explanation – If another party clarifies ambiguous points for them repeatedly, yet the other fails to show any sign of acknowledgement or appreciation for such efforts, then this might indicate an unwillingness to engage meaningfully with contentious issues. <br />4) Attempting to divert attention away from confusing subjects - People sometimes try to change topics if things become complicated, potentially leading the listener astray while trying to protect themselves. They may mention irrelevant or tangential issues, thereby distracting

In [10]:
prompt = """### Instruction: What are some potential implications of using a single-use plastic bottle versus a reusable bottle on both the environment and human health?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Single-Use Plastics vs. Reusables <br />The environmental impacts of using a single use plastic bottle as opposed to an eco friendly water bottles can be broken down into four main categories: landfill waste, ocean pollution, energy consumption during production, and potentially harmful chemicals used in their manufacture. By comparison with reusable options like glass or stainless steel bottles which are durable enough to last for years, there is also a financial advantage in terms of cost savings over time that comes from switching away from disposing of thousands of throwaway plastic bottles each year (often made only once before being discarded).<br /><br />Landfill Waste: Single-use plastic bottles have become synonymous with littered roadsides, parks, oceans and other areas where they take centuries to decompose and release harmful greenhouse gases throughout decomposition. Disposal of these items contributes to deforestation because paper bags must often be produced when recycling facilities cannot accept them. While certain types of plastic containers may be compostable after reuse or breakdown naturally, many of those available today do not biodegrade readily. The resultant

In [11]:
prompt = """### Instruction: What factors would you consider when designing an inclusive and accessible public transportation system?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Inclusion is important for all people, especially in terms of their access to public transport. There are several elements that can be considered when creating a more user-friendly transit service: <br /><br />1. Designed For Accessibility - All aspects related to the physical infrastructure should aim at making it easier for people with different abilities or disabilities such as wheelchairs users or vision impaired passengers, among others, to use them. This includes ensuring that the platforms, stations and vehicles have sufficient space and proper equipment (elevators, ramps etc.) to accommodate those who need it. <br />2. Accessible Information – Clear communication channels like Braille signage, tactile maps, audio announcements, videos, information kiosks or even social media pages where commuters can ask questions are essential. They allow everyone to obtain accurate and timely updates about schedule changes, delays, interruptions or other relevant events affecting services without having to rely on a third party to convey this critical information accurately. <br />3. Flexible Schedule & Routes – A flexible schedule allows riders to adapt their trips according to their needs and preferences by providing options to change routes or times during